In [1]:
import pandas as pd
import numpy as np
from scipy.stats import zscore
import statsmodels.api as sm
import random


In [2]:
# Read data from the Excel file
input_file = 'Returns_short_interest_data.xlsx'
input_sheet = 'GW variables'
input_sheet1= 'Returns'

# Load data from 'GW variables' sheet
gw_variables = pd.read_excel(input_file, sheet_name=input_sheet, usecols="K,Q", skiprows=1224, nrows=504, header=None)
gw_variables1 = pd.read_excel(input_file, sheet_name=input_sheet, usecols="K,Q", skiprows=1225, nrows=504, header=None)

Rfree_lag = gw_variables.iloc[:, 0]
R_VW_SP500 = gw_variables1.iloc[:, 1]

# Load data from 'Returns' sheet
returns = pd.read_excel(input_file, sheet_name=input_sheet1 , usecols= "C, D, E", skiprows=1, nrows=504, header=None)
R_EW_SP500 = returns.iloc[:,0]
R_VW_CRSP = returns.iloc[:,1]
R_EW_CRSP = returns.iloc[:,2]

# Calculate the equity risk premium for each investment strategy
r_VW_SP500 = np.log(1 + R_VW_SP500) - np.log(1 + Rfree_lag)
r_EW_SP500 = np.log(1 + R_EW_SP500) - np.log(1 + Rfree_lag)
r_VW_CRSP = np.log(1 + R_VW_CRSP) - np.log(1 + Rfree_lag)
r_EW_CRSP = np.log(1 + R_EW_CRSP) - np.log(1 + Rfree_lag)

# Combine the equity risk premium data for all investment strategies into a single matrix
r = np.column_stack((r_VW_SP500, r_EW_SP500, r_VW_CRSP, r_EW_CRSP))

/Users/jorgenlunner/opt/anaconda3/lib/python3.9/site-packages/openpyxl/worksheet/header_footer.py:48: UserWarning: Cannot parse header or footer so it will be ignored
  warn("""Cannot parse header or footer so it will be ignored""")
/Users/jorgenlunner/opt/anaconda3/lib/python3.9/site-packages/openpyxl/worksheet/_reader.py:312: UserWarning: Unknown extension is not supported and will be removed
  warn(msg)
/Users/jorgenlunner/opt/anaconda3/lib/python3.9/site-packages/openpyxl/worksheet/header_footer.py:48: UserWarning: Cannot parse header or footer so it will be ignored
  warn("""Cannot parse header or footer so it will be ignored""")
/Users/jorgenlunner/opt/anaconda3/lib/python3.9/site-packages/openpyxl/worksheet/_reader.py:312: UserWarning: Unknown extension is not supported and will be removed
  warn(msg)
/Users/jorgenlunner/opt/anaconda3/lib/python3.9/site-packages/openpyxl/worksheet/_reader.py:312: UserWarning: Unknown extension is not supported and will be removed
  warn(msg)


In [3]:
# Load Goyal-Welch predictor data, 1973:01-2014:12
GW = np.load('Program_generate_GW_predictors.npy')
GW_standardize = zscore(GW, ddof=1)

In [4]:
# Load data from 'Short interest' sheet
short_interest = pd.read_excel(input_file, sheet_name='Short interest', usecols= "B, C, D, E", skiprows=1, nrows=504, header=None)
EWSI = short_interest[1].to_numpy()
SI_alt = short_interest.to_numpy()

# Calculate log values
log_EWSI = np.log(EWSI).reshape(-1,1)
log_SI_alt = np.log(SI_alt)

/Users/jorgenlunner/opt/anaconda3/lib/python3.9/site-packages/openpyxl/worksheet/_reader.py:312: UserWarning: Unknown extension is not supported and will be removed
  warn(msg)


In [5]:
# Detrend log short interest series

T = len(log_EWSI)
SII_EWSI = np.empty((T, 4))
SII_alt = np.empty((T, log_SI_alt.shape[1]))
trend = np.arange(1, T+1)

# Linear regression
X_linear = sm.add_constant(trend)
results_linear = sm.OLS(log_EWSI, X_linear).fit()
SII_EWSI[:,0] = zscore(results_linear.resid, ddof=1)

# Linear regression for each column of log_SI_alt
for i in range(log_SI_alt.shape[1]):
    X_linear_i = sm.add_constant(trend)
    results_linear_i = sm.OLS(log_SI_alt[:,i], X_linear_i).fit()
    SII_alt[:,i] = zscore(results_linear_i.resid, ddof=1)

# Quadratic and cubic regression
X_quadratic = sm.add_constant(np.column_stack((trend, trend**2)))
X_cubic = sm.add_constant(np.column_stack((trend, trend**2, trend**3)))
results_quadratic = sm.OLS(log_EWSI, X_quadratic).fit()
results_cubic = sm.OLS(log_EWSI, X_cubic).fit()
SII_EWSI[:,1] = zscore(results_quadratic.resid, ddof=1)
SII_EWSI[:,2] = zscore(results_cubic.resid, ddof=1)

# Moving average
MA_size = 60
SII_EWSI_SD = np.empty((T, 1))
SII_EWSI_SD[:] = np.nan

for t in range(MA_size - 1, T):
    SII_EWSI_SD[t] = log_EWSI[t] - np.mean(log_EWSI[t - MA_size + 1 : t + 1])

SII_EWSI[MA_size - 1 :, 3] = zscore(SII_EWSI_SD[MA_size - 1 :], ddof=1).flatten()

In [6]:
# Compute cumulative returns

h = [1, 3, 6, 12]

# Assuming r is a 2D NumPy array
num_rows, num_columns = r.shape

r_h = np.empty((num_rows, len(h), num_columns))
r_h[:] = np.nan

for j in range(len(h)):
    for k in range(num_columns):
        for t in range(num_rows - (h[j] - 1)):
            r_h[t, j, k] = np.mean(r[t:t + h[j], k])

In [7]:
# Define subsamples observations

indicator_sub = np.zeros((len(r), 7))

index_sub_1 = np.arange(0, (1982 - 1972) * 12)  # 1973:01-1982:12
indicator_sub[index_sub_1, 0] = 1

index_sub_2 = np.arange((1982 - 1972) * 12, (1992 - 1972) * 12)  # 1983:01-1992:12
indicator_sub[index_sub_2, 1] = 1

index_sub_3 = np.arange((1992 - 1972) * 12, (2002 - 1972) * 12)  # 1993:01-2002:12
indicator_sub[index_sub_3, 2] = 1

index_sub_4 = np.arange((2002 - 1972) * 12, (2014 - 1972) * 12)  # 2003:01-2014:12
indicator_sub[index_sub_4, 3] = 1

index_sub_5 = np.arange((2007 - 1972) * 12, (2014 - 1972) * 12)  # 2008:01-2014:12
indicator_sub[index_sub_5, 4] = 1

index_sub_6 = np.arange((2008 - 1972) * 12, (2014 - 1972) * 12)  # 2009:01-2014:12
indicator_sub[index_sub_6, 5] = 1

index_sub_7 = np.arange((1982 - 1972) * 12, (2007 - 1972) * 12)  # 1973:01-2007:12
indicator_sub[index_sub_7, 6] = 1

In [8]:
beta_hat_alt_detrend = np.empty((SII_EWSI.shape[1], 4, len(h)))
beta_hat_alt_return = np.empty((r.shape[1], 4, len(h)))
beta_hat_alt_SI = np.empty((SII_alt.shape[1], 4, len(h)))
beta_hat_subsample = np.empty((indicator_sub.shape[1], 4, len(h)))

for j in range(len(h)):
    # Alternative detrending
    for k in range(SII_EWSI.shape[1]):
        if k == SII_EWSI.shape[1]-1: 
            X_j_k = np.column_stack((np.ones(len(r) - (MA_size - 1) - h[j]), -SII_EWSI[MA_size-1:-h[j], k]))
            if j == 0:                            
                results_j_k = sm.OLS(endog=100 * r_h[MA_size:, j, 0].reshape(-1,1), exog=X_j_k).fit(cov_type='HAC', cov_kwds={'maxlags': h[j]})
            else: 
                results_j_k = sm.OLS(endog=100*r_h[MA_size:-h[j]+1, j, 0],
                             exog=X_j_k).fit(cov_type='HAC', cov_kwds={'maxlags': h[j]})  
        else:
            X_j_k = np.column_stack((np.ones((len(r) - h[j],1)), -SII_EWSI[:-h[j], k]))
            if j == 0:
                results_j_k = sm.OLS(endog=100 * r_h[1:, j, 0].reshape(-1,1), exog=X_j_k).fit(cov_type='HAC', cov_kwds={'maxlags': h[j]})
            else:
                results_j_k = sm.OLS(endog=100 * r_h[1:len(r) - h[j]+1, j, 0].reshape(-1,1), exog=X_j_k).fit(cov_type='HAC', cov_kwds={'maxlags': h[j]})
        beta_hat_alt_detrend[k, :, j] = [results_j_k.params[1],
                                results_j_k.tvalues[1],
                                np.nan,
                                100 * results_j_k.rsquared]

      # Alternative market portfolio returns
    for k in range(r.shape[1]):
        X_j_k = np.column_stack((np.ones((len(r)-h[j], 1)), -SII_EWSI[:(-h[j]), 0]))
        if j == 0: 
            results_j_k = sm.OLS(endog=100 * r_h[1:, j, k].reshape(-1,1), exog=X_j_k).fit(cov_type='HAC', cov_kwds={'maxlags': h[j]})
        else: 
            results_j_k = sm.OLS(endog= 100 * r_h[1:len(r) - h[j]+1, j, k].reshape(-1,1), exog= X_j_k).fit(cov_type='HAC', cov_kwds={'maxlags': h[j]})
        beta_hat_alt_return[k, :, j] = [results_j_k.params[1],
                                results_j_k.tvalues[1],
                                np.nan,
                                100 * results_j_k.rsquared]  
        
      # Alternative short interest measures  
    for k in range(SII_alt.shape[1]):
        X_j_k = np.column_stack((np.ones(len(r) - h[j]), -SII_alt[:-h[j], k]))
        if j == 0:
            results_j_k = sm.OLS(endog=100 * r_h[1:, j, 0].reshape(-1,1), exog=X_j_k).fit(cov_type='HAC', cov_kwds={'maxlags': h[j]})
        else:
            results_j_k = sm.OLS(endog=100 * r_h[1:len(r) - h[j] + 1, j, 0].reshape(-1,1), exog=X_j_k).fit(cov_type='HAC', cov_kwds={'maxlags': h[j]})
        beta_hat_alt_SI[k, :, j] = [results_j_k.params[1],
                                    results_j_k.tvalues[1],
                                    np.nan,
                                    100 * results_j_k.rsquared]
        
      # Subsample analysis 
    for i in range(indicator_sub.shape[1]): 
        index_sub_i = np.where(indicator_sub[:, i] == 1)[0]
        X_i_j = np.column_stack((np.ones(len(index_sub_i)), -SII_EWSI[index_sub_i, 0]))
        y_i_j = r_h[index_sub_i, j, 0]
        if j== 0: 
            results_i_j = sm.OLS(100 * y_i_j[1:], X_i_j[:-h[j], :]).fit(cov_type='HAC', cov_kwds={'maxlags': h[j]})
        else:
            results_i_j = sm.OLS(100 * y_i_j[1:-h[j]+1], X_i_j[:-h[j], :]).fit(cov_type='HAC', cov_kwds={'maxlags': h[j]})
        beta_hat_subsample[i, :, j] = [results_i_j.params[1], results_i_j.tvalues[1], np.nan, 100 * results_i_j.rsquared]
    

In [9]:
# Compute fixed-regressor wild bootstrap p-values
X_sink = np.column_stack((GW_standardize, SII_EWSI[:, 0]))
X_sink = np.delete(X_sink, [3, 10], axis=1)
X_sink = np.column_stack((np.ones(len(r)), X_sink))
epsilon_hat = np.empty((len(r_h) - 1, r.shape[1]), dtype=np.float64)
epsilon_hat[:] = np.nan

for k in range(r.shape[1]):
    results_k = sm.OLS(r[1:, k], X_sink[:-1, :]).fit()
    epsilon_hat[:, k] = results_k.resid

In [10]:
B = 1000
beta_hat_tstat_alt_detrend_star = np.empty((B, SII_EWSI.shape[1], len(h)), dtype=np.float64)
beta_hat_tstat_alt_return_star = np.empty((B, r_h.shape[2], len(h)), dtype=np.float64)
beta_hat_tstat_alt_SI_star = np.empty((B, SI_alt.shape[1], len(h)), dtype=np.float64)
beta_hat_tstat_subsample_star = np.empty((B, indicator_sub.shape[1], len(h)), dtype=np.float64)
beta_hat_tstat_alt_detrend_star[:] = np.nan
beta_hat_tstat_alt_return_star[:] = np.nan
beta_hat_tstat_alt_SI_star[:] = np.nan
beta_hat_tstat_subsample_star[:] = np.nan

In [11]:
random.seed(0)  # for reproducibility

for b in range(B):
    u_star_b = np.random.randn(len(r) - 1)
    r_star_b = np.empty((len(r), r.shape[1]), dtype=np.float64)
    r_star_b[:] = np.nan
    
    for k in range(r.shape[1]):
        r_star_b[:, k] = np.concatenate(([r[0, k]], r[:, k].mean() + epsilon_hat[:, k] * u_star_b))
    
    r_h_star_b = np.empty((len(r_h), len(h), r.shape[1]), dtype=np.float64)
    r_h_star_b[:] = np.nan
    
    for j in range(len(h)):
        for k in range(r.shape[1]):
            for t in range(len(r_h) - (h[j] - 1)):
                r_h_star_b[t, j, k] = r_star_b[t:t + h[j], k].mean()
    
    for j in range(len(h)):
        for k in range(SII_EWSI.shape[1]):
            if k == SII_EWSI.shape[1] - 1:
                X_j_k = np.column_stack((np.ones(len(r) - (MA_size - 1) - h[j]), -SII_EWSI[MA_size - 1:-h[j], k]))
                if j == 0:
                    results_j_k_star_b = sm.OLS(100*r_h_star_b[MA_size:, j, 0], X_j_k).fit(cov_type='HAC', cov_kwds={'maxlags': h[j]})
                else: 
                    results_j_k_star_b = sm.OLS(100*r_h_star_b[MA_size:-h[j] + 1, j, 0], X_j_k).fit(cov_type='HAC', cov_kwds={'maxlags': h[j]})
            else:
                X_j_k = np.column_stack((np.ones(len(r) - h[j]), -SII_EWSI[:-h[j], k]))
                if j== 0: 
                    results_j_k_star_b = sm.OLS(100*r_h_star_b[1:, j, 0], X_j_k).fit(cov_type='HAC', cov_kwds={'maxlags': h[j]})
                else: 
                    results_j_k_star_b = sm.OLS(100*r_h_star_b[1:-h[j] + 1, j, 0], X_j_k).fit(cov_type='HAC', cov_kwds={'maxlags': h[j]})
            beta_hat_tstat_alt_detrend_star[b, k, j] = results_j_k_star_b.tvalues[1]
        
        for k in range(r.shape[1]):
            X_j_k = np.column_stack((np.ones(len(r) - h[j]), -SII_EWSI[:-h[j], 0]))
            if j == 0: 
                results_j_k_star_b = sm.OLS(100*r_h_star_b[1:, j, k], X_j_k).fit(cov_type='HAC',cov_kwds={'maxlags':h[j]})
            else: 
                results_j_k_star_b = sm.OLS(100*r_h_star_b[1:-h[j] + 1, j, k], X_j_k).fit(cov_type='HAC',cov_kwds={'maxlags':h[j]})
            beta_hat_tstat_alt_return_star[b, k, j] = results_j_k_star_b.tvalues[1]
        
        for k in range(SI_alt.shape[1]):
            X_j_k = np.column_stack((np.ones(len(r) - h[j]), -SI_alt[:-h[j], k]))
            if j == 0:
                results_j_k_star_b = sm.OLS(100*r_h_star_b[1:, j, 0], X_j_k).fit(cov_type='HAC',cov_kwds={'maxlags':h[j]})
            else:
                results_j_k_star_b = sm.OLS(100*r_h_star_b[1:-h[j] + 1, j, 0], X_j_k).fit(cov_type='HAC',cov_kwds={'maxlags':h[j]})
            beta_hat_tstat_alt_SI_star[b, k, j] = results_j_k_star_b.tvalues[1]
        
        for i in range(indicator_sub.shape[1]):
            index_sub_i = np.where(indicator_sub[:, i] == 1)[0]
            X_i_j = np.column_stack((np.ones(len(index_sub_i)), -SII_EWSI[index_sub_i, 0]))
            y_i_j_star_b = r_h_star_b[index_sub_i, j, 0]
            if j == 0:
                results_i_j_star_b = sm.OLS(100*y_i_j_star_b[1:], X_i_j[:-h[j], :]).fit(cov_type='HAC',cov_kwds={'maxlags':h[j]})
            else: 
                results_i_j_star_b = sm.OLS(100*y_i_j_star_b[1:-h[j] + 1], X_i_j[:-h[j], :]).fit(cov_type='HAC',cov_kwds={'maxlags':h[j]})
            beta_hat_tstat_subsample_star[b, i, j] = results_i_j_star_b.tvalues[1]


In [12]:
for j in range(len(h)):
    for k in range(SII_EWSI.shape[1]):
        beta_hat_alt_detrend[k, 2, j] = np.sum(beta_hat_tstat_alt_detrend_star[:, k, j] > beta_hat_alt_detrend[k, 1, j]) / B
    
    for k in range(r.shape[1]):
        beta_hat_alt_return[k, 2, j] = np.sum(beta_hat_tstat_alt_return_star[:, k, j] > beta_hat_alt_return[k, 1, j]) / B
    
    for k in range(SI_alt.shape[1]):
        beta_hat_alt_SI[k, 2, j] = np.sum(beta_hat_tstat_alt_SI_star[:, k, j] > beta_hat_alt_SI[k, 1, j]) / B
    
    for i in range(indicator_sub.shape[1]):
        beta_hat_subsample[i, 2, j] = np.sum(beta_hat_tstat_subsample_star[:, i, j] > beta_hat_subsample[i, 1, j]) / B

In [13]:
# Write results to excel file 
output_file = 'Returns_short_interest_results.xlsx'
output_sheet = 'Additional in-sample PR results'

with pd.ExcelWriter(output_file, engine='openpyxl', mode='a',if_sheet_exists='overlay') as writer:
    pd.DataFrame(beta_hat_alt_detrend[:,:,0]).to_excel(writer, sheet_name=output_sheet, startrow=3, startcol=4, header=False, index=False)
    pd.DataFrame(beta_hat_alt_detrend[:,:,1]).to_excel(writer, sheet_name=output_sheet, startrow=3, startcol=9, header=False, index=False)
    pd.DataFrame(beta_hat_alt_detrend[:,:,2]).to_excel(writer, sheet_name=output_sheet, startrow=3, startcol=14, header=False, index=False)
    pd.DataFrame(beta_hat_alt_detrend[:,:,3]).to_excel(writer, sheet_name=output_sheet, startrow=3, startcol=19, header=False, index=False)
    pd.DataFrame(beta_hat_alt_return[:,:,0]).to_excel(writer, sheet_name=output_sheet, startrow=8, startcol=4, header=False, index=False)
    pd.DataFrame(beta_hat_alt_return[:,:,1]).to_excel(writer, sheet_name=output_sheet, startrow=8, startcol=9, header=False, index=False)
    pd.DataFrame(beta_hat_alt_return[:,:,2]).to_excel(writer, sheet_name=output_sheet, startrow=8, startcol=14, header=False, index=False)
    pd.DataFrame(beta_hat_alt_return[:,:,3]).to_excel(writer, sheet_name=output_sheet, startrow=8, startcol=19, header=False, index=False)
    pd.DataFrame(beta_hat_alt_SI[:,:,0]).to_excel(writer, sheet_name=output_sheet, startrow=13, startcol=4, header=False, index=False)
    pd.DataFrame(beta_hat_alt_SI[:,:,1]).to_excel(writer, sheet_name=output_sheet, startrow=13, startcol=9, header=False, index=False)
    pd.DataFrame(beta_hat_alt_SI[:,:,2]).to_excel(writer, sheet_name=output_sheet, startrow=13, startcol=14, header=False, index=False)
    pd.DataFrame(beta_hat_alt_SI[:,:,3]).to_excel(writer, sheet_name=output_sheet, startrow=13, startcol=19, header=False, index=False)
    pd.DataFrame(beta_hat_subsample[:,:,0]).to_excel(writer, sheet_name=output_sheet, startrow=18, startcol=4, header=False, index=False)
    pd.DataFrame(beta_hat_subsample[:,:,1]).to_excel(writer, sheet_name=output_sheet, startrow=18, startcol=9, header=False, index=False)
    pd.DataFrame(beta_hat_subsample[:,:,2]).to_excel(writer, sheet_name=output_sheet, startrow=18, startcol=14, header=False, index=False)
    pd.DataFrame(beta_hat_subsample[:,:,3]).to_excel(writer, sheet_name=output_sheet, startrow=18, startcol=19, header=False, index=False)